In [ ]:
class ImprovedBoundingBoxProcessor2(nn.Module):
    def __init__(self, num_classes, alpha=0.25, gamma=2.0):
        super().__init__()
        self.num_classes = num_classes
        self.alpha = alpha
        self.gamma = gamma
        self.criterion = SmoothL1Loss(reduction='sum')


    def loss_forward(self, predictions, targets, conf_threshold=0.6, iou_threshold=0.5):
        locations, confidences = predictions
        # batch_size = len(locations)
        total_loss = 0

        batch_loss = self.process_single_batch(
            locations, confidences,
            targets['boxes'], targets['labels'],
            conf_threshold, iou_threshold
        )
        print("Batch loss: ", batch_loss)
        total_loss += batch_loss

        return total_loss

    def process_single_batch(self, loc, conf, target_boxes, target_labels, conf_threshold, iou_threshold):
        device = loc.device
        target_boxes = target_boxes.to(device)
        target_labels = target_labels.to(device)
        # pred_locs = torch.zeros(size = (target_boxes.size(0), target_boxes.size(1),target_boxes.size(2)), device = device)
        # Ensure conf is of shape (num_predictions, num_classes)
        if conf.dim() == 3:
            conf = conf.squeeze(0)

        # confidence_scores, predicted_classes = conf.max(dim=1)
        # print(f"Shape before applying max: {conf.shape}")
        confidence_scores, predicted_classes = conf.max(dim=1)
        print(f"Shape after applying max: {confidence_scores.shape}, {predicted_classes.shape}")
        print("The shape of locations and confidenc is ",loc.shape,conf.shape)
        mask = confidence_scores > conf_threshold

        if not mask.any():
            # mask
            print("Not found any mask.")
            return torch.tensor(0.001, device=device,requires_grad=True)

        # Apply mask to the second dimension of loc
        filtered_loc = loc[:, mask, :]  # This preserves the batch dimension if present
        filtered_conf = conf[mask]
        filtered_scores = confidence_scores[mask]
        print(f"The shape of filtered score and conf is {filtered_conf.shape},{filtered_scores.shape}")

        if filtered_loc.numel() == 0 or target_boxes.numel() == 0:
            print("No locations found")
            return torch.tensor(0.001, device=device,requires_grad=True)

        # Squeeze the batch dimension if it exists
        print(f"The shape of filtered_loc and target_boxes is {filtered_loc.shape},{target_boxes.shape}")


        tgtbox_expanded = target_boxes.unsqueeze(2).expand(-1, target_boxes.size(1), filtered_loc.size(1), 4)  # (1, 3, 5, 4)
        predloc_expanded = filtered_loc.unsqueeze(1).expand(-1, target_boxes.size(1), filtered_loc.size(1), 2)  # (1, 3, 5, 2)
        loc_determined = torch.zeros(size=(target_boxes.size(0), target_boxes.size(1) * filtered_loc.size(1), target_boxes.size(2)),device=device)
        loc_determined[:, :, 0] = (tgtbox_expanded[:, :, :, 0] * predloc_expanded[:, :, :, 0]).view(1, -1)
        loc_determined[:, :, 1] = (tgtbox_expanded[:, :, :, 1] * predloc_expanded[:, :, :, 1]).view(1, -1)
        loc_determined[:, :, 2] = (tgtbox_expanded[:, :, :, 2] * predloc_expanded[:, :, :, 0]).view(1, -1)
        loc_determined[:, :, 3] = (tgtbox_expanded[:, :, :, 3] * predloc_expanded[:, :, :, 1]).view(1, -1)
        # ious = box_iou(filtered_loc, target_boxes)
        # max_ious, max_indices = ious.max(dim=1)
        score = filtered_conf[:,0]
        # print("Shape of conf is ",score,filtered_conf.squeeze.shape)
        pred_loc_final = loc_determined.squeeze(0)
        nms_boxes = nms(pred_loc_final,score,iou_threshold)
        # positive_mask = max_ious > iou_threshold
        if not nms_boxes.any():
            print("No mask.")
            return torch.tensor(0.001, device=device,requires_grad=True)

        matched_loc = pred_loc_final[nms_boxes,:]
        matched_conf = filtered_conf[nms_boxes,:]
        k = target_labels.shape[0]
        matched_conf,indices= topk(matched_conf,k,dim=0)
        matched_conf = (matched_conf[:,0]> 0.5).to(torch.float64)

        matched_loc = matched_loc[indices,:]
        matched_target_boxes = target_boxes
        matched_target_labels = target_labels.to(torch.float64)
        # pred_locs[:, 0] = matched_loc[:, 0] * matched_target_boxes[:, 0]
        # pred_locs[:, 1] = matched_loc[:, 1] * matched_target_boxes[:, 1]
        # pred_locs[:, 2] = matched_loc[:, 0] * matched_target_boxes[:, 2]
        # pred_locs[:, 3] = matched_loc[:, 1] * matched_target_boxes[:, 3]
        # pred_box = matched_loc
        loc_loss = self.criterion(matched_loc, matched_target_boxes,)
        conf_loss = self.focal_loss(matched_conf, matched_target_labels)


        num_positives = nms_boxes.sum().float()
        total_loss = (loc_loss + conf_loss) / num_positives
        print("Reached here.")
        del score,matched_loc,target_boxes,target_labels,
        del num_positives,loc_loss,conf_loss,matched_conf,matched_target_boxes,matched_target_labels,filtered_conf,filtered_scores,filtered_loc,conf_threshold,iou_threshold
        return total_loss
    def focal_loss(self, pred, target):
        # print(f"The values of the target boxes are: {target.dtype} and prediction are: {pred}")
        ce_loss = F.cross_entropy(pred, target, reduction='none')
        p_t = torch.exp(-ce_loss)
        loss = self.alpha * (1 - p_t) ** self.gamma * ce_loss
        return loss.sum()



In [7]:
import json
import os

def filter_annotations(input_json_path, output_json_path):
    """
    Filters out annotations that have more than one bounding box from a JSON file.
    
    Parameters:
    - input_json_path: str, path to the input JSON file with annotations.
    - output_json_path: str, path to save the filtered JSON file.
    """

    # Step 1: Load the JSON file
    with open(input_json_path, 'r') as f:
        data = json.load(f)

    # Assuming the annotation structure is something like:
    # {
    #     "images": [...],
    #     "annotations": [
    #         {
    #             "image_id": ...,
    #             "bbox": [...]
    #         }, ...
    #     ]
    # }
    
    filtered_annotations = []

    # Step 2: Iterate through annotations
    for annotation in data['annotations']:
        # Step 3: Check if the annotation contains more than one bounding box
        if len(annotation['bbox']) == 1:  # If it contains exactly one bounding box
            filtered_annotations.append(annotation)

    # Step 4: Replace the original annotations with the filtered list
    data['annotations'] = filtered_annotations

    # Step 5: Save the updated JSON data to the output path
    with open(output_json_path, 'w') as f:
        json.dump(data, f, indent=4)

    print(f"Filtered annotations saved to {output_json_path}")

# Example usage



In [9]:
input_json_path = "D:/image_detection_data/annotations/annotation.json"  # Replace with your input JSON path
output_json_path = "D:/image_detection_data/annotation/annotation.json"  # Replace with your output JSON path

filter_annotations(input_json_path, output_json_path)

Filtered annotations saved to D:/image_detection_data/annotation/annotation.json


In [10]:
ann = json.load(open("D:/image_detection_data/annotation/annotation.json"))

In [11]:
ann.keys()

dict_keys(['images', 'annotations', 'categories'])

In [14]:
len(ann['annotations'])

494264

In [15]:
import pandas as pd
import plotly.express as px

# Load your data from the CSV file
data = pd.read_csv("ULTRA_LOSS.csv")

# Create an interactive line chart
fig = px.line(data, x="Batch", y="Loss", title="Loss Over Batches")

# Show the plot
fig.show()